# README (Ignore if you are running on Mac/Linux)

If you are running on Windows, make sure you have started the Jupyter Notebook in a Bash shell.
Moreover, all the requirements below must be installed in this Bash (compatible) shell.

This can be achieved as follows:

1. Enable and install WSL(2) for Windows 10/11 [official documentation](https://docs.microsoft.com/en-us/windows/wsl/install)
    * On newer builds of W10/11 you can install WSL by running the following command in an *administrator* PowerShell terminal. Which will install by default an Ubuntu instance of WSL.
    ```bash
   wsl --install
    ```
2. Start the Ubuntu Bash shell by searching for `Bash` under Start, or by running `bash` in a (normal) PowerShell terminal.

Using a Bash terminal as started under step 2 above, you can install the Requirements as described below as if you are running it under Linux or Ubuntu/Debian.

## Requirements
These requirements may also be installed on Windows, however, development has only been tested on Linux/macOS.

Before we get started, first make sure to install all the required tools. We provide two lists below, one needed for setting up the testbed. And one for developing code to use with the testbed. Feel free to skip the installation of the second list, and return at a later point in time.


### Deployment

 > ⚠️ All dependencies must be installed in a Bash-compatible shell. For Windows users also see [above](#read-me)
Make sure to install a recent version of each of the dependencies.


 * (Windows only) Install every dependency in a Windows Subsystem for the Linux, Bash shell (see also README above).
 * GCloud SDK
    - Follow the installation instructions [here](https://cloud.google.com/sdk/docs/install), follow either the Linux installation instruction, or your OS/Distribution specific instructions.
    - Initialize the SDK with `gcloud init`, if prompted you may ignore to set/create a default/first project.
    - ⚠️ Run the command `gcloud auth application-default login`
        - ℹ️ We need to run this command to utilize your login credentials programmatically with terraform. This is needed as we will use these to impersonate a service account during the creation and setup of the Kubernetes cluster.
    - ⚠️ Run the command `gcloud components install beta`
        - ℹ️ We need to run this command to list the billing account IDs and enable billing. Currently, these features fall under beta access.
    - ⚠️ Run the command `gcloud components install gke-gcloud-auth-plugin`
        - ℹ️ We need to run this command to retrieve cluster configurations (to be used by `kubectl` and `helm`)
    - ⚠️ Run the command `gcloud auth configure-docker`
        - ℹ️ We need to run this command to push container images with docker to your project's container registry
 * Kubectl (>= 1.22.0)
 * Helm (>= 3.9.4)
 * Terraform (>= 1.2.8)
 * Python3.9/10
   * jupyter, ipython, bash_kernel
```bash
pip3 install -r requirements-jupyter.txt
python3 -m bash_kernel.install
```

### Development
For development, the following tools are needed/recommended:

 * Docker (>= 18.09).
    - If you don't have experience with using Docker, we recommend following [this](https://docs.docker.com/get-started/) tutorial.
 * Python3.9
 * pip3
 * JetBrains PyCharm

# Preparation

To make sure we can request resources on Google Cloud Platform (GCP), perform the following;

1. Create a GCP account on [https://cloud.google.com](https://cloud.google.com), using a Google account
2. Redeem your academic coupon on GCP, see Brightspace for information on obtaining the \\$50 academic coupon, or use the free \\$300 credits for new users provided by Google.


3. Make sure to use the `Bash` kernel, not a Python or other kernel. For those on windows machines, make sure to launch the `jupyter notebook` server from a bash-compliant command line, we recommend Windows Subsystem for Linux.

⚠️ Make sure to run this Notebook within a cloned repository, not standalone/downloaded from GitHub.


# Deployment

⚠️ This notebook assumes that commands are executed in order. Executing the provided commands multiple times should not result in issues. However, re-running cells with `cd` commands, or altering cells (other than variables as instructed) may result in unexpected behaviour.

## Getting started

First, we will set a few variables used **throughout** the project. We set them in this notebook for convenience, but they are also set to some example default values in configuration files for the project. If you change any of these, make sure to change the corresponding variables as well in;

* [`../terraform/terraform-gke/variables.tf`](../terraform/terraform-gke/variables.tf)
* [`../terraform/terraform-dependencies/variables.tf`](../terraform/terraform-dependencies/variables.tf)


> ⚠️ As you have changed the `PROJECT_ID` parameter to a unique project name, also change the `project_id` variable in the following files. This allows you to run `terraform apply` without having to override the default value for the project.

> ℹ️ Any variable changed here can also be provided to `terraform` using the `-var` flag, i.e.  `-var terraform_variable=$BASH_VARIABLE`. An example for setting the `project_id` variable is also provided later.

In [2]:
# VARIABLES THAT NEEDS TO BE SET

##################
### CHANGE ME! ###
##################
PROJECT_ID="test-bed-fltk69420"

# DEFAULT VARIABLES
ACCOUNT_ID="terraform-iam-service-account"
PRIVILEGED_ACCOUNT_ID="${ACCOUNT_ID}@${PROJECT_ID}.iam.gserviceaccount.com"
CLUSTER_NAME="fltk-testbed-cluster"
DEFAULT_POOL="default-node-pool"
EXPERIMENT_POOL="medium-fltk-pool-1"
REGION="us-central1-c"

TERRAFORM_GKE_DIR="../terraform/terraform-gke"
TERRAFORM_DEPENDENCIES_DIR="../terraform/terraform-dependencies"

## Project creation

Next, we create a project using the `PROJECT_ID` variable and get all the billing account information.

⁉️ (Ignore if using a pre-existing GCP Project) If the command below does not complete successfully, make sure to change the `PROJECT_ID` variable in the previous cell and re-run it.

In [2]:
gcloud projects create $PROJECT_ID --set-as-default
gcloud beta billing accounts list # Copy the Account ID of the account

ERROR: (gcloud.projects.create) Project creation failed. The project ID you specified is already in use by another project. Please try an alternative ID.
ACCOUNT_ID            NAME                OPEN  MASTER_ACCOUNT_ID
019099-71A491-340D22  My Billing Account  True


Copy the billing account identifier, e.g. `015594-41687F-092941`, and assign to the variable in the cell below

In [3]:
##################
### CHANGE ME! ###
##################
BILLING_ACCOUNT="019099-71A491-340D22"

Setup billing and enable services, this will allow us to create a GKE cluster (Google managed Kubernetes cluster), and push and pull containers to our private container repo.

In [20]:
# Setup billing to project
gcloud beta billing projects link $PROJECT_ID --billing-account $BILLING_ACCOUNT
# Enable services now billing is enabled
gcloud services enable compute container --project $PROJECT_ID

billingAccountName: billingAccounts/019099-71A491-340D22
billingEnabled: true
name: projects/test-bed-fltk69420/billingInfo
projectId: test-bed-fltk69420
Operation "operations/acat.p2-1072090310122-ac2e8143-38bb-4ba3-8a5d-01255b139126" finished successfully.


## Creating a service-account

Create service account that has the minimum set of permissions for creating and managing a cluster. This service account
will be used to create the cluster, and deploy the dependencies that we use.

During the deployment we will make use of impersonation, to let *your* account utilize the service-account. For more information about this practise, see also [this](https://cloud.google.com/blog/topics/developers-practitioners/using-google-cloud-service-account-impersonation-your-terraform-code) blog by Google.

In [21]:
# Helper function to quickly enable gcp roles, assumes $PRIVILEGED_ACCOUNT_ID and $PROJECT_ID to be set.
function enable_gcp_role () {
  ROLE=$1
  gcloud projects add-iam-policy-binding \
    $PROJECT_ID \
    --member="serviceAccount:$PRIVILEGED_ACCOUNT_ID" \
    --role="roles/$ROLE"
}

# Create service-account
gcloud iam service-accounts create $ACCOUNT_ID --display-name="Terraform service account" --project ${PROJECT_ID}

# Allow the service account to use the the set of roles below.
enable_gcp_role "compute.viewer"                # Allow the service account to see active resources
enable_gcp_role "storage.objectViewer"          # Allow the service account/managed resources to pull from gcr.io (your code)
enable_gcp_role "compute.networkAdmin"          # Needed for setting up private network
enable_gcp_role "compute.securityAdmin"         # Needed for GKE
enable_gcp_role "container.clusterViewer"       # Needed for GKE
enable_gcp_role "container.clusterAdmin"        # Needed for GKE
enable_gcp_role "container.developer"           # Needed for GKE
enable_gcp_role "iam.serviceAccountAdmin"       # Needed for GKE
enable_gcp_role "iam.serviceAccountUser"        # Needed for GKE


ERROR: (gcloud.iam.service-accounts.create) Resource in projects [test-bed-fltk69420] is the subject of a conflict: Service account terraform-iam-service-account already exists within project projects/test-bed-fltk69420.
- '@type': type.googleapis.com/google.rpc.ResourceInfo
  resourceName: projects/test-bed-fltk69420/serviceAccounts/terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
Updated IAM policy for project [test-bed-fltk69420].
bindings:
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.networkAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.securityAdmin
- members:
  - serviceAccount:service-1072090310122@compute-system.iam.gserviceaccount.com
  role: roles/compute.serviceAgent
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.

  role: roles/iam.serviceAccountAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/iam.serviceAccountUser
- members:
  - user:chris.s.bras@gmail.com
  role: roles/owner
- members:
  - serviceAccount:service-1072090310122@gcp-sa-pubsub.iam.gserviceaccount.com
  role: roles/pubsub.serviceAgent
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/storage.objectViewer
etag: BwXrLCB-vcE=
version: 1
Updated IAM policy for project [test-bed-fltk69420].
bindings:
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.networkAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.securityAdmin
- members:
  - serviceAccount:service-1072090310122@compute-system.iam.gserviceaccount.com
  role: roles/compute.serviceAgent
-

  - serviceAccount:1072090310122@cloudservices.gserviceaccount.com
  role: roles/editor
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/iam.serviceAccountAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/iam.serviceAccountUser
- members:
  - user:chris.s.bras@gmail.com
  role: roles/owner
- members:
  - serviceAccount:service-1072090310122@gcp-sa-pubsub.iam.gserviceaccount.com
  role: roles/pubsub.serviceAgent
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/storage.objectViewer
etag: BwXrLCEdofk=
version: 1
Updated IAM policy for project [test-bed-fltk69420].
bindings:
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com
  role: roles/compute.networkAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk69

## Enable impersonation
With the service account created, we must enable impersonation, to allow the main account of the project to make use of the service account. For more information see also the [`add-iam-policy-binding`](https://cloud.google.com/sdk/gcloud/reference/iam/service-accounts/add-iam-policy-binding) reference.

Assign your `google_account` mail to the `OWNER_MAIL` variable, and run the command box below.

In [22]:
##################
### CHANGE ME! ###
##################
OWNER_MAIL="chris.s.bras@gmail.com"

gcloud iam service-accounts add-iam-policy-binding $PRIVILEGED_ACCOUNT_ID \
 --member="user:$OWNER_MAIL" \
 --role=roles/iam.serviceAccountTokenCreator \
 --project $PROJECT_ID

Updated IAM policy for serviceAccount [terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com].
bindings:
- members:
  - user:chris.s.bras@gmail.com
  role: roles/iam.serviceAccountTokenCreator
etag: BwXrLCFtC_g=
version: 1


To enable using your account's credentials, run the command below. This will open in a new tab/open the link that is displayed. Afterwards you can use your own credentials to impersonate the service account. 

You can, for example, also allow other google users (such as project members) to work with your cluster in this way.

In [23]:
gcloud auth application-default login

Your browser has been opened to visit:

    https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=764086051850-6qr4p6gpi6hn506pt8ejuq83di341hur.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A8085%2F&scope=openid+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fuserinfo.email+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fcloud-platform+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fsqlservice.login+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Faccounts.reauth&state=QfjgAl81uz86JL3NahHzhe2ZhkJ4QX&access_type=offline&code_challenge=mmXj6NuMkCysu8nW47DxunjFzTwLq8lTKUr12njltpM&code_challenge_method=S256


Credentials saved to file: [/Users/Chris/.config/gcloud/application_default_credentials.json]

These credentials will be used by any library that requests Application Default Credentials (ADC).

Quota project "test-bed-fltk69420" was added to ADC which can be used by Google client libraries for billing and quota. Note that some services may still bill the project owning the 

## Creating a Google managed cluster (GKE)
To create the cluster, first change the active directory to the `terraform-gke` directory.

⚠️ Creating a cluster will incur billing cost on your project, by default the cluster will be small to minimize costs during this tutorial. Forgetting to `destroy` or scale down the cluster may result in quickly spending your academic coupon.

Init the directory, to initialize the Terraform module.

In [26]:
terraform -chdir=$TERRAFORM_GKE_DIR init 

Initializing modules...

Initializing the backend...

Initializing provider plugins...
- Reusing previous version of hashicorp/google from the dependency lock file
- Reusing previous version of hashicorp/kubernetes from the dependency lock file
- Reusing previous version of hashicorp/google-beta from the dependency lock file
- Reusing previous version of hashicorp/random from the dependency lock file
- Using previously-installed hashicorp/kubernetes v2.14.0
- Using previously-installed hashicorp/google-beta v4.40.0
- Using previously-installed hashicorp/random v3.4.3
- Using previously-installed hashicorp/google v4.40.0

Terraform has been successfully initialized!

You may now begin working with Terraform. Try running "terraform plan" to see
any changes that are required for your infrastructure. All Terraform commands
should now work.

If you ever set or change modules or backend configuration for Terraform,
rerun this command to reinitialize your working directory. If you forget, oth

Next, we can check whether we can create a cluster. No warnings or errors should occur during this process. It may take a while to complete.

> ⚠️ We provide the project_id variable from `terraform/terraform-gke` manually, and also change the default value.

⁉️ If the command below does not complete successfully, e.g. after raising a `403` error, make sure that you have successfully created the project with `gcloud` earlier.


In [28]:
terraform -chdir=$TERRAFORM_GKE_DIR plan -var project_id=$PROJECT_ID

module.gke.random_string.cluster_service_account_suffix: Refreshing state... [id=naea]
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com]
module.gke.data.google_compute_zones.available: Reading...
data.google_client_config.default: Reading...
module.gke.data.google_container_engine_versions.region: Reading...
module.gcp-network.module.vpc.google_compute_network.network: Refreshing state... [id=projects/test-bed-fltk69420/global/networks/gcp-private-network]
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk69420/regions//zones/]
module.gcp-network.module.subnets.google_compute_subnetwork.subnetwork["us-central1/gcp-private-subnetwork"]: Refreshing state... [id=projects/test-bed-fltk69420/regions/us-central1/subnetworks/gcp-private-subnetwork]
module.gke.data.google_co

          - cluster_secondary_range_name  = "ip-range-pods" -> null
          - services_ipv4_cidr_block      = "192.168.64.0/18" -> null
          - services_secondary_range_name = "ip-range-scv" -> null
        }

      - logging_config {
          - enable_components = [
              - "SYSTEM_COMPONENTS",
              - "WORKLOADS",
            ] -> null
        }

      - maintenance_policy {
          - daily_maintenance_window {
              - duration   = "PT4H0M0S" -> null
              - start_time = "05:00" -> null
            }
        }

      - master_auth {
          - cluster_ca_certificate = "LS0tLS1CRUdJTiBDRVJUSUZJQ0FURS0tLS0tCk1JSUVMRENDQXBTZ0F3SUJBZ0lRYStyaTA1UUdmUWRaNXZRUHJJaTN5ekFOQmdrcWhraUc5dzBCQVFzRkFEQXYKTVMwd0t3WURWUVFERXlRelpXSTBNemxpWkMwME1XSmtMVFF6TTJJdFlqbGlNaTAzTkRjNE56WTNOekUyTjJNdwpJQmNOTWpJeE1ERTJNVGt3TnpJNFdoZ1BNakExTWpFd01EZ3lNREEzTWpoYU1DOHhMVEFyQmdOVkJBTVRKRE5sCllqUXpPV0prTFRReFltUXRORE16WWkxaU9XSXlMVGMwTnpnM05qYzNNVFkzWXpDQ0FhSXdEUVlKS29aSWh2

              - labels            = {} -> null
              - local_ssd_count   = 0 -> null
              - machine_type      = "e2-medium" -> null
              - metadata          = {
                  - "disable-legacy-endpoints" = "true"
                } -> null
              - oauth_scopes      = [
                  - "https://www.googleapis.com/auth/logging.write",
                  - "https://www.googleapis.com/auth/monitoring",
                ] -> null
              - preemptible       = false -> null
              - service_account   = "terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com" -> null
              - spot              = false -> null
              - tags              = [
                  - "gke-fltk-testbed-cluster",
                  - "gke-fltk-testbed-cluster-default-pool",
                  - "default-node-pool",
                ] -> null
              - taint             = [] -> null

              - shielded_instance_config {
        

          - node_count                  = 1 -> null
          - node_locations              = [
              - "us-central1-c",
            ] -> null
          - version                     = "1.21.14-gke.7100" -> null

          - autoscaling {
              - max_node_count       = 4 -> null
              - min_node_count       = 0 -> null
              - total_max_node_count = 0 -> null
              - total_min_node_count = 0 -> null
            }

          - management {
              - auto_repair  = true -> null
              - auto_upgrade = true -> null
            }

          - node_config {
              - disk_size_gb      = 64 -> null
              - disk_type         = "pd-standard" -> null
              - guest_accelerator = [] -> null
              - image_type        = "COS_CONTAINERD" -> null
              - labels            = {
                  - "cluster_name" = "fltk-testbed-cluster"
                  - "node_pool"    = "medium-fltk-pool-1"
                } -

          - total_min_node_count = 0 -> null
        }

      - management {
          - auto_repair  = true -> null
          - auto_upgrade = true -> null
        }

      - node_config {
          - disk_size_gb      = 64 -> null
          - disk_type         = "pd-standard" -> null
          - guest_accelerator = [] -> null
          - image_type        = "COS_CONTAINERD" -> null
          - labels            = {
              - "cluster_name"      = "fltk-testbed-cluster"
              - "default-node-pool" = "true"
              - "node_pool"         = "default-node-pool"
            } -> null
          - local_ssd_count   = 0 -> null
          - machine_type      = "e2-medium" -> null
          - metadata          = {
              - "cluster_name"             = "fltk-testbed-cluster"
              - "disable-legacy-endpoints" = "true"
              - "node_pool"                = "default-node-pool"
            } -> null
          - oauth_scopes      = [
              - "https:/

          - spot              = false -> null
          - tags              = [
              - "gke-fltk-testbed-cluster",
              - "gke-fltk-testbed-cluster-medium-fltk-pool-1",
            ] -> null
          - taint             = [
              - {
                  - effect = "PREFER_NO_SCHEDULE"
                  - key    = "fltk.node"
                  - value  = "medium-e2"
                },
            ] -> null

          - shielded_instance_config {
              - enable_integrity_monitoring = true -> null
              - enable_secure_boot          = false -> null
            }

          - workload_metadata_config {
              - mode = "GKE_METADATA" -> null
            }
        }

      - timeouts {
          - create = "45m" -> null
          - delete = "45m" -> null
          - update = "45m" -> null
        }

      - upgrade_settings {
          - max_surge       = 1 -> null
          - max_unavailable = 0 -> null
        }
    }


Unless you have made e

            }
        }

      + mesh_certificates {
          + enable_certificates = (known after apply)
        }

      + monitoring_config {
          + enable_components = (known after apply)
        }

      + network_policy {
          + enabled = false
        }

      + node_config {
          + boot_disk_kms_key = (known after apply)
          + disk_size_gb      = (known after apply)
          + disk_type         = (known after apply)
          + guest_accelerator = (known after apply)
          + image_type        = (known after apply)
          + labels            = (known after apply)
          + local_ssd_count   = (known after apply)
          + machine_type      = (known after apply)
          + metadata          = (known after apply)
          + min_cpu_platform  = (known after apply)
          + node_group        = (known after apply)
          + oauth_scopes      = (known after apply)
          + preemptible       = (known after apply)
          + service_account  

      + version                     = (known after apply)

      + autoscaling {
          + max_node_count = 100
          + min_node_count = 0
        }

      + management {
          + auto_repair  = true
          + auto_upgrade = true
        }

      + node_config {
          + disk_size_gb      = 64
          + disk_type         = "pd-standard"
          + guest_accelerator = []
          + image_type        = "COS_CONTAINERD"
          + labels            = {
              + "cluster_name"      = "fltk-testbed-cluster"
              + "default-node-pool" = "true"
              + "node_pool"         = "default-node-pool"
            }
          + local_ssd_count   = 0
          + machine_type      = "e2-medium"
          + metadata          = {
              + "cluster_name"             = "fltk-testbed-cluster"
              + "disable-legacy-endpoints" = "true"
              + "node_pool"                = "default-node-pool"
            }
          + min_cpu_platform  = (known

Note: You didn't use the -out option to save this plan, so Terraform can't
guarantee to take exactly these actions if you run "terraform apply" now.


When the previous command completes successfully, we can start the deployment. Depending on any changes you may have done, this might take a while.

By default, this will create a private zonal cluster consisting of two node pools.

> ⚠️ A regional cluster (multi-zonal) will incur an additional fee of \\$ 0.10 /hour per managed (GKE) cluster. The **first** zonal cluster is free of this charge.

> ⚠️ By default spot/preemptive nodes are disabled. You can experiment by setting `spot` to true in the `tf` files. Note, however, that the default implementations provided in the testbed do not allow for recovery from getting spun down and rescheduled. Moreover, this may result in poor availability during busy hours in the region in which you deploy your cluster.


In [29]:
terraform -chdir=$TERRAFORM_GKE_DIR apply -auto-approve -var project_id=$PROJECT_ID

module.gke.random_string.cluster_service_account_suffix: Refreshing state... [id=naea]
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com]
data.google_client_config.default: Reading...
module.gke.data.google_container_engine_versions.region: Reading...
module.gke.data.google_compute_zones.available: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk69420/regions//zones/]
module.gcp-network.module.vpc.google_compute_network.network: Refreshing state... [id=projects/test-bed-fltk69420/global/networks/gcp-private-network]
module.gcp-network.module.subnets.google_compute_subnetwork.subnetwork["us-central1/gcp-private-subnetwork"]: Refreshing state... [id=projects/test-bed-fltk69420/regions/us-central1/subnetworks/gcp-private-subnetwork]
module.gke.data.google_co

          - cluster_secondary_range_name  = "ip-range-pods" -> null
          - services_ipv4_cidr_block      = "192.168.64.0/18" -> null
          - services_secondary_range_name = "ip-range-scv" -> null
        }

      - logging_config {
          - enable_components = [
              - "SYSTEM_COMPONENTS",
              - "WORKLOADS",
            ] -> null
        }

      - maintenance_policy {
          - daily_maintenance_window {
              - duration   = "PT4H0M0S" -> null
              - start_time = "05:00" -> null
            }
        }

      - master_auth {
          - cluster_ca_certificate = "LS0tLS1CRUdJTiBDRVJUSUZJQ0FURS0tLS0tCk1JSUVMRENDQXBTZ0F3SUJBZ0lRYStyaTA1UUdmUWRaNXZRUHJJaTN5ekFOQmdrcWhraUc5dzBCQVFzRkFEQXYKTVMwd0t3WURWUVFERXlRelpXSTBNemxpWkMwME1XSmtMVFF6TTJJdFlqbGlNaTAzTkRjNE56WTNOekUyTjJNdwpJQmNOTWpJeE1ERTJNVGt3TnpJNFdoZ1BNakExTWpFd01EZ3lNREEzTWpoYU1DOHhMVEFyQmdOVkJBTVRKRE5sCllqUXpPV0prTFRReFltUXRORE16WWkxaU9XSXlMVGMwTnpnM05qYzNNVFkzWXpDQ0FhSXdEUVlKS29aSWh2

              - labels            = {} -> null
              - local_ssd_count   = 0 -> null
              - machine_type      = "e2-medium" -> null
              - metadata          = {
                  - "disable-legacy-endpoints" = "true"
                } -> null
              - oauth_scopes      = [
                  - "https://www.googleapis.com/auth/logging.write",
                  - "https://www.googleapis.com/auth/monitoring",
                ] -> null
              - preemptible       = false -> null
              - service_account   = "terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com" -> null
              - spot              = false -> null
              - tags              = [
                  - "gke-fltk-testbed-cluster",
                  - "gke-fltk-testbed-cluster-default-pool",
                  - "default-node-pool",
                ] -> null
              - taint             = [] -> null

              - shielded_instance_config {
        

          - node_count                  = 1 -> null
          - node_locations              = [
              - "us-central1-c",
            ] -> null
          - version                     = "1.21.14-gke.7100" -> null

          - autoscaling {
              - max_node_count       = 4 -> null
              - min_node_count       = 0 -> null
              - total_max_node_count = 0 -> null
              - total_min_node_count = 0 -> null
            }

          - management {
              - auto_repair  = true -> null
              - auto_upgrade = true -> null
            }

          - node_config {
              - disk_size_gb      = 64 -> null
              - disk_type         = "pd-standard" -> null
              - guest_accelerator = [] -> null
              - image_type        = "COS_CONTAINERD" -> null
              - labels            = {
                  - "cluster_name" = "fltk-testbed-cluster"
                  - "node_pool"    = "medium-fltk-pool-1"
                } -

          - total_min_node_count = 0 -> null
        }

      - management {
          - auto_repair  = true -> null
          - auto_upgrade = true -> null
        }

      - node_config {
          - disk_size_gb      = 64 -> null
          - disk_type         = "pd-standard" -> null
          - guest_accelerator = [] -> null
          - image_type        = "COS_CONTAINERD" -> null
          - labels            = {
              - "cluster_name"      = "fltk-testbed-cluster"
              - "default-node-pool" = "true"
              - "node_pool"         = "default-node-pool"
            } -> null
          - local_ssd_count   = 0 -> null
          - machine_type      = "e2-medium" -> null
          - metadata          = {
              - "cluster_name"             = "fltk-testbed-cluster"
              - "disable-legacy-endpoints" = "true"
              - "node_pool"                = "default-node-pool"
            } -> null
          - oauth_scopes      = [
              - "https:/

          - spot              = false -> null
          - tags              = [
              - "gke-fltk-testbed-cluster",
              - "gke-fltk-testbed-cluster-medium-fltk-pool-1",
            ] -> null
          - taint             = [
              - {
                  - effect = "PREFER_NO_SCHEDULE"
                  - key    = "fltk.node"
                  - value  = "medium-e2"
                },
            ] -> null

          - shielded_instance_config {
              - enable_integrity_monitoring = true -> null
              - enable_secure_boot          = false -> null
            }

          - workload_metadata_config {
              - mode = "GKE_METADATA" -> null
            }
        }

      - timeouts {
          - create = "45m" -> null
          - delete = "45m" -> null
          - update = "45m" -> null
        }

      - upgrade_settings {
          - max_surge       = 1 -> null
          - max_unavailable = 0 -> null
        }
    }


Unless you have made e

            }
        }

      + mesh_certificates {
          + enable_certificates = (known after apply)
        }

      + monitoring_config {
          + enable_components = (known after apply)
        }

      + network_policy {
          + enabled = false
        }

      + node_config {
          + boot_disk_kms_key = (known after apply)
          + disk_size_gb      = (known after apply)
          + disk_type         = (known after apply)
          + guest_accelerator = (known after apply)
          + image_type        = (known after apply)
          + labels            = (known after apply)
          + local_ssd_count   = (known after apply)
          + machine_type      = (known after apply)
          + metadata          = (known after apply)
          + min_cpu_platform  = (known after apply)
          + node_group        = (known after apply)
          + oauth_scopes      = (known after apply)
          + preemptible       = (known after apply)
          + service_account  

      + version                     = (known after apply)

      + autoscaling {
          + max_node_count = 100
          + min_node_count = 0
        }

      + management {
          + auto_repair  = true
          + auto_upgrade = true
        }

      + node_config {
          + disk_size_gb      = 64
          + disk_type         = "pd-standard"
          + guest_accelerator = []
          + image_type        = "COS_CONTAINERD"
          + labels            = {
              + "cluster_name"      = "fltk-testbed-cluster"
              + "default-node-pool" = "true"
              + "node_pool"         = "default-node-pool"
            }
          + local_ssd_count   = 0
          + machine_type      = "e2-medium"
          + metadata          = {
              + "cluster_name"             = "fltk-testbed-cluster"
              + "disable-legacy-endpoints" = "true"
              + "node_pool"                = "default-node-pool"
            }
          + min_cpu_platform  = (known

module.gke.google_container_cluster.primary: Still creating... [20s elapsed]
module.gke.google_container_cluster.primary: Still creating... [30s elapsed]
module.gke.google_container_cluster.primary: Still creating... [40s elapsed]
module.gke.google_container_cluster.primary: Still creating... [50s elapsed]
module.gke.google_container_cluster.primary: Still creating... 0s elapsed]
module.gke.google_container_cluster.primary: Still creating... 10s elapsed]
module.gke.google_container_cluster.primary: Still creating... 20s elapsed]
module.gke.google_container_cluster.primary: Still creating... 30s elapsed]
module.gke.google_container_cluster.primary: Still creating... 40s elapsed]
module.gke.google_container_cluster.primary: Still creating... 50s elapsed]
module.gke.google_container_cluster.primary: Still creating... 0s elapsed]
module.gke.google_container_cluster.primary: Still creating... 10s elapsed]
module.gke.google_container_cluster.primary: Creation complete after 2m16s [id=project

module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Still creating... 50s elapsed]
module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Still creating... 0s elapsed]
module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Creation complete after 5m9s [id=projects/test-bed-fltk69420/locations/us-central1-c/clusters/fltk-testbed-cluster/nodePools/medium-fltk-pool-1]

Apply complete! Resources: 3 added, 0 changed, 0 destroyed.

Outputs:

cluster_identifier = "fltk-testbed-cluster"
kubernetes_endpoint = <sensitive>
private_network_identifier = "gcp-private-network"
subnet_identifier = [
  "gcp-private-subnetwork",
]
subnet_ranges = [
  tolist([
    {
      "ip_cidr_range" = "192.168.0.0/18"
      "range_name" = "ip-range-pods"
    },
    {
      "ip_cidr_range" = "192.168.64.0/18"
      "range_name" = "ip-range-scv"
    },
  ]),
]
terraform_service_account = "terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com"


Next, we add cluster credentials (so you can interact with the cluster through `kubectl` an `helm`).

In [30]:
# Add credentials for interacting with cluster via kubectl
gcloud container clusters get-credentials $CLUSTER_NAME --region $REGION --project $PROJECT_ID

Fetching cluster endpoint and auth data.
kubeconfig entry generated for fltk-testbed-cluster.


⚠️ The cluster by default does not contain any nodes in the node pools, the `initial_node_count` is set to 0.

Lastly, we need to scale up the cluster, as by default we create a cluster with nodepools of size 0.

In [31]:
gcloud config set project $PROJECT_ID

Updated property [core/project].


In [32]:
echo $DEFAULT_POOL

default-node-pool


In [33]:
###
### ! CHANGE ME
###
MAX_NUM_NODES=4

gcloud container clusters update $CLUSTER_NAME --node-pool $DEFAULT_POOL \
    --no-enable-autoscaling --region $REGION --quiet
    
# The high performance node will scale up automatically whenever the workloads are deployed
gcloud container clusters update $CLUSTER_NAME --node-pool $EXPERIMENT_POOL \
    --enable-autoscaling --min-nodes=0 --max-nodes=$MAX_NUM_NODES --region $REGION --quiet

gcloud container clusters resize $CLUSTER_NAME --node-pool $DEFAULT_POOL \
    --num-nodes 1 --region $REGION --quiet


Default change: During creation of nodepools or autoscaling configuration changes for cluster versions greater than 1.24.1-gke.800 a default location policy is applied. For Spot and PVM it defaults to ANY, and for all other VM kinds a BALANCED policy is used. To change the default values use the `--location-policy` flag.
Updating fltk-testbed-cluster...done.                                          
Updated [https://container.googleapis.com/v1/projects/test-bed-fltk69420/zones/us-central1-c/clusters/fltk-testbed-cluster].
To inspect the contents of your cluster, go to: https://console.cloud.google.com/kubernetes/workload_/gcloud/us-central1-c/fltk-testbed-cluster?project=test-bed-fltk69420
Default change: During creation of nodepools or autoscaling configuration changes for cluster versions greater than 1.24.1-gke.800 a default location policy is applied. For Spot and PVM it defaults to ANY, and for all other VM kinds a BALANCED policy is used. To change the default values use the `--l

### Changing deployment

To save cost, or run different experiments, you might want to change the configuration of your cluster. This can be achieved by modifying the cluster configuration in the [`terraform-gke/main.tf`](../terraform/terraform-gke/main.tf) configuration file. You can change the default node-pools, create additional node pools with taints (to allow for scheduling on specific nodes/pools) and much more.

After finishing your changes, simply run the following commands

```bash
# Use `plan` to check your configuration
terraform plan
# Check to see if your changes are as expected, terraform will show what will be created/removed.

# If the changes are as you expect, apply the changes.
terraform apply #-auto-approve
```

Depending on the number of changes, this may take some time.

## Installing dependencies
Lastly, we need to install the dependencies on our cluster. First change the directories, and then run the `init`, `plan` and `apply` commands as we did for creating the GKE cluster.

Init the directory, to initialize the Terraform module.

In [34]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR init -reconfigure


Initializing the backend...

Initializing provider plugins...
- Reusing previous version of hashicorp/helm from the dependency lock file
- Reusing previous version of kbst/kustomization from the dependency lock file
- Reusing previous version of hashicorp/google from the dependency lock file
- Reusing previous version of gavinbunney/kubectl from the dependency lock file
- Reusing previous version of hashicorp/kubernetes from the dependency lock file
- Using previously-installed hashicorp/google v4.40.0
- Using previously-installed gavinbunney/kubectl v1.14.0
- Using previously-installed hashicorp/kubernetes v2.14.0
- Using previously-installed hashicorp/helm v2.7.0
- Using previously-installed kbst/kustomization v0.9.0

Terraform has been successfully initialized!

You may now begin working with Terraform. Try running "terraform plan" to see
any changes that are required for your infrastructure. All Terraform commands
should now work.

If you ever set or change modules or backend conf

Check to see if we can plan the deployment. This will setup the following:

* Kubeflow training operator (used to deploy and manage PyTorchTrainJobs programmatically)
* NFS-provisioner (used to enable logging on a persistent `ReadWriteMany` PVC in the cluster)


In [35]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR plan -var project_id=$PROJECT_ID

data.kustomization_build.training_operator: Reading...
helm_release.nfs_client_provisioner: Refreshing state... [id=nfs-server]
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com]
data.google_client_config.default: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk69420/regions//zones/]
data.google_container_cluster.testbed_cluster: Reading...
data.google_container_cluster.testbed_cluster: Read complete after 1s [id=projects/test-bed-fltk69420/locations/us-central1-c/clusters/fltk-testbed-cluster]
data.kustomization_build.training_operator: Read complete after 3s [id=a294ea9a3d4f626ec1ec55aac66b4a486f682fe5dbec2eadf58d30baee14a8f66a3ec2674c0e2d9a40e7bc191f878f010393849f4581c6a4189bc41761abab89]
kustomization_resource.training_operator["rbac.authorization.k8s

                
                  mountOptions:
                    - vers=3
                
                  ## ReclaimPolicy field of the class, which can be either Delete or Retain
                  reclaimPolicy: Delete
                
                ## For RBAC support:
                rbac:
                  create: true
                
                  ## Ignored if rbac.create is true
                  ##
                  serviceAccountName: default
                
                resources: {}
                  # limits:
                  #  cpu: 100m
                  #  memory: 128Mi
                  # requests:
                  #  cpu: 100m
                  #  memory: 128Mi
                
                nodeSelector: {}
                
                tolerations: []
                
                affinity: {}
            EOT,
        ]
      + verify                     = false
      + version                    = "1.1.3"
      + wait                     

                                                  + type        = "string"
                                                }
                                              + mainContainer   = {
                                                  + description = "MainContainer specifies name of the main container which executes the MPI code."
                                                  + type        = "string"
                                                }
                                              + mpiReplicaSpecs = {
                                                  + additionalProperties = {
                                                      + description = "ReplicaSpec is a description of the replica"
                                                      + properties  = {
                                                          + replicas      = {
                                                              + description = "Replicas is the desired number of replicas o

                                                                                              + items       = {
                                                                                                  + description = "An empty preferred scheduling term matches all objects with implicit weight 0 (i.e. it's a no-op). A null preferred scheduling term matches no objects (i.e. is also a no-op)."
                                                                                                  + properties  = {
                                                                                                      + preference = {
                                                                                                          + description = "A node selector term, associated with the corresponding weight."
                                                                                                          + properties  = {
                                                  

                                                                                                                              + description = "An array of string values. If the operator is In or NotIn, the values array must be non-empty. If the operator is Exists or DoesNotExist, the values array must be empty. If the operator is Gt or Lt, the values array must have a single element, which will be interpreted as an integer. This array is replaced during a strategic merge patch."
                                                                                                                              + items       = {
                                                                                                                                  + type = "string"
                                                                                                                                }
                                                                                              

...

                                                                                                      + description = "name must match the name of a persistentVolumeClaim in the pod"
                                                                                                      + type        = "string"
                                                                                                    }
                                                                                                }
                                                                                              + required    = [
                                                                                                  + "devicePath",
                                                                                                  + "name",
                                                                                                ]
                                                          

                                                                                }
                                                                              + type        = "array"
                                                                            }
                                                                          + nodeName                      = {
                                                                              + description = "NodeName is a request to schedule this pod onto a specific node. If it is non-empty, the scheduler simply schedules this pod onto that node, assuming that it fits resource requirements."
                                                                              + type        = "string"
                                                                            }
                                                                          + nodeSelector                  = {
                                                       

                                                                              + operator = {
                                                                                  + description = "operator represents a key's relationship to a set of values. Valid operators are In, NotIn, Exists and DoesNotExist."
                                                                                  + type        = "string"
                                                                                }
                                                                              + values   = {
                                                                                  + description = "values is an array of string values. If the operator is In or NotIn, the values array must be non-empty. If the operator is Exists or DoesNotExist, the values array must be empty. This array is replaced during a strategic merge patch."
                                                                         

                              + {
                                  + command         = [
                                      + "/manager",
                                    ]
                                  + env             = [
                                      + {
                                          + name      = "MY_POD_NAMESPACE"
                                          + valueFrom = {
                                              + fieldRef = {
                                                  + fieldPath = "metadata.namespace"
                                                }
                                            }
                                        },
                                      + {
                                          + name      = "MY_POD_NAME"
                                          + valueFrom = {
                                              + fieldRef = {
                                                  + fieldPath = "metadata

                          + "update",
                        ]
                    },
                  + {
                      + apiGroups = [
                          + "",
                        ]
                      + resources = [
                          + "configmaps",
                          + "secrets",
                          + "serviceaccounts",
                        ]
                      + verbs     = [
                          + "create",
                          + "list",
                          + "watch",
                          + "update",
                        ]
                    },
                  + {
                      + apiGroups = [
                          + "scheduling.volcano.sh",
                        ]
                      + resources = [
                          + "podgroups",
                        ]
                      + verbs     = [
                          + "*",
                        ]
                    },
   

When the previous command completes successfully, we can start the deployment. This will install the NFS provisioner and Kubeflow Training Operator dependencies


In [4]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR apply -auto-approve -var project_id=$PROJECT_ID

data.kustomization_build.training_operator: Reading...
helm_release.nfs_client_provisioner: Refreshing state... [id=nfs-server]
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk69420.iam.gserviceaccount.com]
data.google_client_config.default: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk69420/regions//zones/]
data.google_container_cluster.testbed_cluster: Reading...
data.google_container_cluster.testbed_cluster: Read complete after 1s [id=projects/test-bed-fltk69420/locations/us-central1-c/clusters/fltk-testbed-cluster]
data.kustomization_build.training_operator: Read complete after 4s [id=a294ea9a3d4f626ec1ec55aac66b4a486f682fe5dbec2eadf58d30baee14a8f66a3ec2674c0e2d9a40e7bc191f878f010393849f4581c6a4189bc41761abab89]
kustomization_resource.training_operator["rbac.authorization.k8s

## Deploying extractor

Lastly, we deploy the extractor pod, which also provides PVCs which can be used for artifact retrieval.

Retrieval can be done by running

```bash
EXTRACTOR_POD_NAME=$(kubectl get pods -n test -l "app.kubernetes.io/name=fltk.extractor" -o jsonpath="{.items[0].metadata.name}")
kubectl cp -n test $EXTRACTOR_POD_NAME:/opt/federation-lab/logging ./logging
```

For copying from the extractor path `/opt/federation-lab/logging` to a directory locally named `logging`.

First build the docker container, following the instructions of the [readme](https://github.com/JMGaljaard/fltk-testbed#creating-and-uploading-docker-container).


N.B. Make sure to have setup a working authentication provider for docker, such that you can push to your repository.

Run this in a terminal in the content-root directory (so `fltk-testbed` if the project name was not altered).
```bash
python3 -m venv venv
source venv
pip3 install -r requirements-cpu.txt
python3 -m fltk extractor configs/example_cloud_experiment.json
```

Make sure to have run `gcloud auth configure-docker` in an external terminal.

Make sure to allow docker to build/push/run without `sudo` [link](https://cloud.google.com/artifact-registry/docs/docker/authentication).


In [5]:
# Build the docker container with buildkit. Make sure you have Docker Desktop running on Windows/MacOS
DOCKER_BUILDKIT=1 docker build --platform linux/amd64 ../ --tag gcr.io/$PROJECT_ID/fltk


[+] Building 0.0s (0/1)                                                         
[+] Building 0.1s (0/2)                                                         
 => [internal] load build definition from Dockerfile                       0.1s
[+] Building 0.2s (0/2)                                                         
 => [internal] load build definition from Dockerfile                       0.2s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.1s
 => => transferring context:                                               0.0s
[+] Building 0.3s (1/2)                                                         
 => [internal] load build definition from Dockerfile                       0.4s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.2s
 => => transferring context: 34B    

[+] Building 2.5s (2/3)                                                         
 => [internal] load build definition from Dockerfile                       0.4s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          1.8s
[+] Building 2.6s (2/3)                                                         
 => [internal] load build definition from Dockerfile                       0.4s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          1.9s
[+] Building 2.8s (2/3)               

 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2051d9e0 0B / 315.74MB  0.3s
 => [internal] load build context                                          0.3s
 => => transferring context: 110B                                          0.3s
[+] Building 4.2s (4/13)                                                        
 => [internal] load build definition from Dockerfile                       0.4s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => [internal] settings cache mount permissions                            0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63  0.4s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f9917

 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => [internal] settings cache mount permissions                            0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63  1.3s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f99177ad891e68789959b7071ee 742B / 742B  0.0s
 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2051 1.05MB / 315.74MB  1.3s
 => [internal] load build context                                          1.3s
 => => transferring context: 110B                                          1.3s
[+] Building 5.2s (4/13)                                                        
 => [internal] load build definition fr

 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2051 4.19MB / 315.74MB  2.0s
 => [internal] load build context                                          2.0s
 => => transferring context: 3.50MB                                        2.0s
[+] Building 6.0s (4/13)                                                        
 => [internal] load build definition from Dockerfile                       0.4s
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => [internal] settings cache mount permissions                            0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63  2.2s
 => => resolve docker.io/bitnami/pytorc

...

 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f99177ad891e68789959b7071ee 742B / 742B  0.0s
 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2 315.74MB / 315.74MB  45.4s
 => => extracting sha256:2f068dd64383f912b6384e186607393ea7e1c2051d9e048  31.0s
 => [internal] load build context                                         20.5s
 => => transferring context: 152.57MB                                     20.2s
 => [stage-0 2/8] WORKDIR /opt/federation-lab                              1.5s
 => [stage-0 3/8] ADD data/ data/                                          6.6s
 => [stage-0 4/8] COPY requirements-cpu.txt ./requirements.txt             0.1s
 => [stage-0 5/8] RUN --mount=type=cache,target=/root/.cache/pip,mode=0  129.8s
 => [stage-0 6/8] ADD fltk fltk                                            0.4s
 => [stage-0 7/8] ADD configs configs   

 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f6  77.6s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f99177ad891e68789959b7071ee 742B / 742B  0.0s
 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2 315.74MB / 315.74MB  45.4s
 => => extracting sha256:2f068dd64383f912b6384e186607393ea7e1c2051d9e048  31.0s
 => [internal] load build context                                         20.5s
 => => transferring context: 152.57MB                                     20.2s
 => [stage-0 2/8] WORKDIR /opt/federation-lab                              1.5s
 => [stage-0 3/8] ADD data/ data/                                          6.6s
 => [stage-0 4/8] COPY requirements-cpu.

 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f6  77.6s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f99177ad891e68789959b7071ee 742B / 742B  0.0s
 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2 315.74MB / 315.74MB  45.4s
 => => extracting sha256:2f068dd64383f912b6384e186607393ea7e1c2051d9e048  31.0s
 => [internal] load build context                                         20.5s
 => => transferring context: 152.57MB   

 => => exporting layers                                                    6.5s
[+] Building 226.6s (13/14)                                                     
 => => transferring dockerfile: 37B                                        0.0s
 => [internal] load .dockerignore                                          0.3s
 => => transferring context: 34B                                           0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          3.1s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:a475535f6  77.6s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:a475535f63b50ee881  0.0s
 => => sha256:a475535f63b50ee88136f99177ad891e68789959b7071ee 742B / 742B  0.0s
 => => sha256:ac1b21ac055cd759c5fd12486bae6cef4d841c0d92c 7.21kB / 7.21kB  0.0s
 => => sha256:2f068dd64383f912b6384e186607393ea7e1c2 315.74MB / 315.74MB  45.4s
 => => extracting sha256:2f068dd64383f9

 => [stage-0 6/8] ADD fltk fltk                                            0.4s
 => [stage-0 7/8] ADD configs configs                                      0.1s
 => [stage-0 8/8] ADD experiments experiments                              0.1s
 => exporting to image                                                     6.8s
 => => exporting layers                                                    6.8s
 => => writing image sha256:ffcf2d03d79adc1d6b0f3217e714ede7c1edabc55a90d  0.0s
 => => naming to gcr.io/test-bed-fltk69420/fltk                            0.0s


In [6]:
docker push gcr.io/test-bed-fltk69420/fltk

Using default tag: latest
The push refers to repository [gcr.io/test-bed-fltk69420/fltk]

54d19bf4: Preparing 
3804f4c6: Preparing 
188a25a7: Preparing 
3972bda7: Preparing 
6903c5ef: Preparing 
ae8c4c18: Preparing 
7ad16c58: Preparing 
fd0cda0b: Preparing 
latest: digest: sha256:2b4eaa9c384b20ca580b936412a0cb27c95dd5ba1949720d96cda63c68cd63a9 size: 2207


In [39]:
# Install the extractor, and set the projectName to $PROJECT_ID.
# In case you get a warning regarding the namespace test, this means that the dependencies have not been properly installed.
# Make sure to check whether you have enough resources available, and re-run the installation of dependencies. (see above).
helm uninstall -n test extractor
# Deploy extractor, in test namespace with updated image reference (--set overwrites values from `fltk-values.yaml`).
helm install extractor ../charts/extractor -f ../charts/fltk-values.yaml --namespace test --set provider.projectName=$PROJECT_ID

W1021 21:19:32.218168   91463 gcp.go:119] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.26+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
Error: uninstall: Release not loaded: extractor: release: not found
W1021 21:19:32.987189   91464 gcp.go:119] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.26+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
NAME: extractor
LAST DEPLOYED: Fri Oct 21 21:19:34 2022
NAMESPACE: test
STATUS: deployed
REVISION: 1
TEST SUITE: None
NOTES:
Get the FLTK extractors Tensorboard URL by running:

export POD_NAME=$(kubectl get pods -n test -l "app.kubernetes.io/name=fltk.extractor" -o jsonpath="{.items[0].metadata.name}")
echo http://localhost:6006/
kubectl -n test port-forward $POD_NAME 6006:6006


## Testing the deployment

To make sure that the deployment went OK, we can run the following command to test whether we can use Pytorch-Training operators.

This will create a simple deployment using a Kubeflow pytorch example job.

This will create a small (1 master, 1 client) training job on mnist on your cluster. You can follow the deployment by navigating to your cluster on [cloud.google.com](cloud.google.com)

In [68]:
# This cell is optional, but the next shell should show that a pytorch train job is created.
kubectl create -f https://raw.githubusercontent.com/kubeflow/training-operator/master/examples/pytorch/simple.yaml

pytorchjob.kubeflow.org/pytorch-simple created


In [41]:
# Retrieve all CRD Pytorchjob from Kubeflow.
kubectl get pytorchjobs.kubeflow.org --all-namespaces

# Alternatively, we can remove all jobs, this will remove all information and logs as well.
kubectl delete pytorchjobs.kubeflow.org --all-namespaces --all

NAMESPACE   NAME                                            STATE       AGE
test        trainjob-09913294-cb89-4197-a77c-c9e946791bbe   Succeeded   4h28m
test        trainjob-a5077bd0-18fa-43b0-b65d-a76cf82cb83e   Failed      4h28m
test        trainjob-c76fc545-0cc4-4081-8f27-a25737372ed0   Created     4h28m
pytorchjob.kubeflow.org "trainjob-09913294-cb89-4197-a77c-c9e946791bbe" deleted
pytorchjob.kubeflow.org "trainjob-a5077bd0-18fa-43b0-b65d-a76cf82cb83e" deleted
pytorchjob.kubeflow.org "trainjob-c76fc545-0cc4-4081-8f27-a25737372ed0" deleted


# Cleaning up

## Scaling down the cluster

This is the preferred way to scale down.
Scale node pools down to prevent idle resource utilization.

In [40]:
gcloud container clusters resize $CLUSTER_NAME --node-pool $DEFAULT_POOL \
     --num-nodes 0 --region $REGION --quiet

gcloud container clusters resize $CLUSTER_NAME --node-pool $EXPERIMENT_POOL \
    --num-nodes 0 --region $REGION --quiet

Resizing fltk-testbed-cluster...done.


Updated [https://container.googleapis.com/v1/projects/test-bed-fltk69420/zones/us-central1-c/clusters/fltk-testbed-cluster].
Resizing fltk-testbed-cluster...done.                                          
Updated [https://container.googleapis.com/v1/projects/test-bed-fltk69420/zones/us-central1-c/clusters/fltk-testbed-cluster].


## Destroying the cluster

> ⚠️ THIS WILL REMOVE YOUR CLUSTER AND DATA STORED ON IT. For this tutorial's purpose destroying your cluster is not an issue. For testing/developing, we recommend manually scaling your cluster up and down instead.

To clean up/remove the cluster, we will use the `terraform destroy` command.

 * Running it in `terraform-dependencies` WILL REMOVE the Kubeflow Training-Operator from your cluster.
 * Running it in `terraform-gke` WILL REMOVE YOU ENTIRE CLUSTER.

You can uncomment the commands below to remove the cluster, or run the command in a terminal in the [`../terraform/terraform-gke`](../terraform/terraform-gke) directory.

> ⚠️ It is recommended to scale down the cluster/nodepools rather then destroying, refer to the last code block.

In [ ]:
# THIS WILL REMOVE/TEARDOWN YOUR CLUSTER, ONLY RECOMMENDED FOR TESTING THE DEPLOYMENT

terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR destroy -auto-approve -var project_id=$PROJECT_ID

terraform -chdir=$TERRAFORM_GKE_DIR destroy -auto-approve -var project_id=$PROJECT_ID